In [1]:
%cd /ibex/user/slimhy/PADS/code/

/ibex/user/slimhy/PADS/code


In [2]:
# Add "3DCoMPaT" to the path
import sys
sys.path.append("jupyter/3DCoMPaT/")
from compat3D import ShapeLoader

In [3]:
"""
Extracting features into HDF5 files for each split.
"""
import argparse
import numpy as np
import torch

import util.misc as misc
import util.s2vs as s2vs

In [4]:
def get_args_parser():
    parser = argparse.ArgumentParser("Extracting Features", add_help=False)

    # Model parameters
    parser.add_argument(
        "--batch_size",
        default=32,
        type=int,
        help="Batch size per GPU (effective batch size is batch_size * accum_iter * # gpus",
    )
    parser.add_argument(
        "--text_model_name",
        type=str,
        help="Text model name to use",
    )
    parser.add_argument(
        "--ae",
        type=str,
        metavar="MODEL",
        help="Name of autoencoder",
    )
    parser.add_argument(
        "--ae-latent-dim",
        type=int,
        default=512*8,
        help="AE latent dimension",
    )
    parser.add_argument(
        "--ae_pth",
        required=True,
        help="Autoencoder checkpoint"
    )
    parser.add_argument(
        "--point_cloud_size",
        default=2048,
        type=int,
        help="input size"
    )
    parser.add_argument(
        "--fetch_keys",
        action="store_true",
        default=False,
    )
    parser.add_argument(
        "--use_embeds",
        action="store_true",
        default=False,
    )
    parser.add_argument(
        "--intensity_loss",
        action="store_true",
        default=False,
        help="Contrastive edit intensity loss using ground-truth labels.",
    )

    # Dataset parameters
    parser.add_argument(
        "--dataset",
        type=str,
        choices=["graphedits"],
        help="dataset name",
    )
    parser.add_argument(
        "--data_path",
        type=str,
        help="dataset path",
    )
    parser.add_argument(
        "--data_type",
        type=str,
        help="dataset type",
    )
    parser.add_argument(
        "--max_edge_level",
        default=None,
        type=int,
        help="maximum edge level to use",
    )
    parser.add_argument(
        "--device", default="cuda", help="device to use for training / testing"
    )
    parser.add_argument("--seed", default=0, type=int)
    parser.add_argument("--num_workers", default=60, type=int)
    parser.add_argument(
        "--pin_mem",
        action="store_true",
        help="Pin CPU memory in DataLoader for more efficient (sometimes) transfer to GPU.",
    )

    return parser

In [5]:
# Set dummy arg string to debug the parser
call_string = """--ae_pth ckpt/ae_m512.pth \
    --ae kl_d512_m512_l8 \
    --ae-latent-dim 4096 \
    --batch_size 32 \
    --num_workers 8 \
    --device cuda"""
    

# Parse the arguments
args = get_args_parser()
args = args.parse_args(call_string.split())

In [6]:
# Set device and seed
device = torch.device(args.device)
misc.set_all_seeds(args.seed)
torch.backends.cudnn.benchmark = True

# Instantiate autoencoder
ae = s2vs.load_model(args.ae, args.ae_pth, device, torch_compile=True)
ae = ae.eval()

Set seed to 0
Loading autoencoder [ckpt/ae_m512.pth].


In [7]:
import zipfile
from metadata import SHAPENET_CLASSES, COMPAT_CLASSES, COMPAT_TRANSFORMS


ACTIVE_CLASS = "chair"
METADATA_DIR = "/ibex/user/slimhy/3DCoMPaT/3DCoMPaT-v2/metadata"
ZIP_SRC = "/ibex/user/slimhy/surfaces.zip"
ZIP_PATH = "/ibex/user/slimhy/3DCoMPaT/3DCoMPaT_ZIP.zip"
N_POINTS = 2**21
MAX_POINTS = 2**21 # Maximum number of points for a single batch on a A100 GPU


def shapenet_iterator(shape_cls):
    # List all files in the zip file
    with zipfile.ZipFile(ZIP_SRC, 'r') as zip_ref:
        files = zip_ref.namelist()

        for file in files:
            if not file.startswith(SHAPENET_CLASSES[shape_cls]): continue
            if not file.endswith(".npz"): continue
            # Read a specific file from the zip file
            with zip_ref.open(file) as file:
                data = np.load(file)
                yield data["points"].astype(np.float32)
        

def compat_iterator(shape_cls):
    train_dataset = ShapeLoader(
        zip_path=ZIP_PATH,
        meta_dir=METADATA_DIR,
        split="train",
        n_points=N_POINTS,
        shuffle=True,
        seed=0,
        filter_class=COMPAT_CLASSES[shape_cls]
    )

    for shape_id, shape_label, pointcloud, point_part_labels in train_dataset:
        yield COMPAT_TRANSFORMS[shape_cls](pointcloud)

In [8]:
from util.shapeloaders import SingleManifoldDataset

OBJ_DIR = "/ibex/user/slimhy/PADS/data/obj_manifold/"
OBJ_ID = 4

# Initialize the latents
orig_dataset = SingleManifoldDataset(
    OBJ_DIR,
    ACTIVE_CLASS,
    ae.num_inputs,
    normalize=False,
    sampling_method="surface"
)
surface_points, _ = next(orig_dataset[OBJ_ID])
init_latents = s2vs.encode_pc(ae, surface_points).detach()

In [9]:
from schedulefree import AdamWScheduleFree
import torch.nn.functional as F


def optimize_latents(ae, shape_it, init_latents, acc_steps=1, max_iter=100, optimizer=None):
    """
    Optimize input latent codes w.r.t. a single object with optional gradient accumulation.
    """
    latents = init_latents.clone().detach().to(device).requires_grad_(True)
    if optimizer is None:
        optimizer = torch.optim.Adam
    optimizer = optimizer([latents], lr=1e-3)
    
    iter_count = 0
    while iter_count < max_iter:
        optimizer.zero_grad()
        accumulated_loss = 0

        for k in range(acc_steps):
            try:
                surface_points, occs = next(shape_it)
            except StopIteration:
                break

            surface_points = surface_points.to(device)
            logits = s2vs.query_latents(ae, latents, surface_points, use_graph=True).flatten()
            occs = occs.float().flatten().to(device)
            
            loss = F.binary_cross_entropy_with_logits(logits, occs).mean()
            accumulated_loss += loss.item()
            
            # Accumulate gradients without stepping the optimizer
            loss.backward()

        # Step the optimizer
        optimizer.step()

        if iter_count % 10 == 0:
            print(f"Iter {iter_count}: Average Loss {(accumulated_loss / acc_steps):.4f}")
        
        iter_count += 1

    return latents.detach().cpu()


# Instantiate the dataset
shape_dataset = SingleManifoldDataset(
    OBJ_DIR,
    ACTIVE_CLASS,
    N_POINTS,
    normalize=False,
    sampling_method="volume+near_surface",
    contain_method="occnets",
    decimate=True,
    sample_first=False
)

optimized_latents = optimize_latents(
    ae,
    shape_dataset[OBJ_ID],
    init_latents,
    acc_steps=N_POINTS // MAX_POINTS if N_POINTS > MAX_POINTS else 1,
    max_iter=50,
    optimizer=AdamWScheduleFree
)

Iter 0: Average Loss 0.0255
Iter 10: Average Loss 0.0179
Iter 20: Average Loss 0.0158
Iter 30: Average Loss 0.0144
Iter 40: Average Loss 0.0135


In [10]:
from eval.metrics import iou_occupancies, chamfer_distance, f_score
from util.sampling import sample_surface_tpp
from util.contains.inside_mesh import is_inside
from util.misc import d_GPU, show_side_by_side, timer_init, timer_end


def evaluate_reconstruction(
    obj_original,
    rec_mesh,
    latents,
    n_queries=2**21,
    n_queries_chamfer=2**15,
    query_method="occnets"
):
    """
    Compute IoU and Chamfer distance between the original object and the reconstructed mesh.
    - IoU: Computed using [n_queries] random points sampled from the 3D sp  ace.
    - CD: Computed using [n_queries] points sampled from the object surface.
    """
    timer_init("surface_sampling")

    # Sample N_POINTS points from obj_original and rec_mesh
    pc_original = sample_surface_tpp(obj_original, n_queries_chamfer)
    pc_rec = sample_surface_tpp(rec_mesh, n_queries_chamfer)
    chamfer = chamfer_distance(pc_original, pc_rec)
    f_sc = f_score(gt=pc_original, pred=pc_rec)
    
    timer_end()
    timer_init("point_sampling")

    # Sample uniformly n_queries points from 3D space
    point_queries = torch.rand((1, n_queries, 3)).cuda()
    
    timer_end()
    timer_init("predict_occ")
    
    # Get predicted occupancies for each point
    latents = latents.to(device)
    pred_occs = s2vs.predict_occupancies(ae, latents, point_queries, n_queries)

    timer_end()
    timer_init("is_inside")

    # Get ground-truth occupancy for each point
    gt_occs = is_inside(obj_original, point_queries, query_method=query_method)

    timer_end()
    timer_init("iou_occ")

    # Compute IoU between predicted and ground-truth occupancies
    iou = iou_occupancies(pred_occs, gt_occs)
    
    timer_end()
    
    results = {
        "iou": iou.item(),
        "chamfer": chamfer.item(),
        "f_score": f_sc.item()
    }
    
    return results

In [11]:
# Decode the optimized latents
rec_mesh = s2vs.decode_latents(ae, d_GPU(optimized_latents), grid_density=256, batch_size=128**3)

In [12]:
orig_mesh = shape_dataset.obj
evaluate_reconstruction(orig_mesh, rec_mesh, optimized_latents, query_method="occnets")

{'iou': 0.933634340763092,
 'chamfer': 2.059274265775457e-05,
 'f_score': 0.999664306640625}

In [13]:
# Decode the old latents
old_latents = init_latents
old_rec_mesh = s2vs.decode_latents(ae, d_GPU(old_latents), grid_density=256, batch_size=128**3)

In [14]:
evaluate_reconstruction(orig_mesh, old_rec_mesh, old_latents, query_method="occnets")

{'iou': 0.8569450974464417,
 'chamfer': 3.6069708585273474e-05,
 'f_score': 0.9931802153587341}

In [15]:
show_side_by_side(orig_mesh, rec_mesh, old_rec_mesh)

In [16]:
%%capture

# Save bost meshes as obj
orig_mesh.export("orig_mesh.obj")
rec_mesh.export("rec_mesh.obj")
old_rec_mesh.export("old_rec_mesh.obj")